# Hyper parameter search for TD3+BC

In [10]:
!pip install d3rlpy

In [11]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [12]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [13]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [14]:
dataset, states, actions, rewards = get_dataset([i for  i in range(100)], path="../collected_data/rl_purestochastic.txt")

start
[ 0.00000000e+00  7.95731469e+08  1.14110892e-01  2.46000047e-02
 -2.40000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -6.00000000e-01 -6.00000000e-01]
Read chunk # 1 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -4.33891077e-02 -4.23999953e-02
  2.84999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.95938047e-01 -6.00000000e-01 -4.85130982e-02]
Read chunk # 2 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.97089108e-01 -5.19999953e-02
 -1.57000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.84874650e-01  5.98976918e-01 -3.12414656e-01]
Read chunk # 3 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.33189108e-01  1.48000047e-02
  4.99998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.33187685e-01  5.18887883e-01  2.92787205e-01]
Read chunk # 4 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  3.58910892e-01 -5.15999953e-02
  1.93999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000

[ 0.00000000e+00  7.95731469e+08 -2.46489108e-01  3.10000047e-02
 -1.27000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01  3.43385976e-01  4.56053558e-01]
Read chunk # 55 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.32110892e-01  8.60000469e-03
 -6.40001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01  6.00000000e-01  1.94671770e-01]
Read chunk # 56 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.43589108e-01  4.08000047e-02
  1.43999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.92181381e-01  6.00000000e-01  6.00000000e-01]
Read chunk # 57 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.07189108e-01 -2.89999953e-02
 -1.12000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -3.06449248e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 58 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.51108923e-02 -4.29999953e-02
  1.25999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  5.01765492e-

In [15]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -290.4386,
 'std': 158.53566,
 'min': -622.8723,
 'max': 0.0,
 'histogram': (array([ 5,  3,  5,  2,  4,  1,  5,  0,  5,  8, 10,  6, 10,  7,  5,  7,  9,
          7,  0,  1]),
  array([-622.8723  , -591.7287  , -560.5851  , -529.44147 , -498.29785 ,
         -467.15424 , -436.01062 , -404.867   , -373.7234  , -342.57977 ,
         -311.43616 , -280.29254 , -249.14893 , -218.00531 , -186.8617  ,
         -155.71808 , -124.57446 ,  -93.43085 ,  -62.28723 ,  -31.143616,
            0.      ], dtype=float32))}

In [16]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [17]:
from d3rlpy.algos import CQL, TD3PlusBC
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [18]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = TD3PlusBC(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
                actor_encoder_factory = actor_encoder,
                critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+100 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+200 for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_td3bc.pkl", "wb") as f:
            print("most optimal hyper params for td3+bc at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_td3bc.pt")
        model.save_policy("policy_hyperparams_td3bc.pt")


search iteration:  0
using hyper params:  [0.002891174090044179, 0.0015327012075085425, 5.200136024401661e-05, 1]
2022-04-21 21:52.22 [debug    ] RoundIterator is selected.
2022-04-21 21:52.22 [info     ] Directory is created at d3rlpy_logs/TD3PlusBC_20220421215222
2022-04-21 21:52.22 [debug    ] Fitting scaler...              scaler=standard
2022-04-21 21:52.22 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-21 21:52.22 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-21 21:52.22 [warning  ] Skip building models since they're already built.
2022-04-21 21:52.22 [info     ] Parameters are saved to d3rlpy_logs/TD3PlusBC_20220421215222/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'vector', 'params': {'hidden_units': [12, 24, 36, 24, 12], 'activation': 'relu', 'use_batch_norm': True, 'dropout_rate': 0.2, 'use_dense': False}}, 'actor_lea

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:52.28 [info     ] TD3PlusBC_20220421215222: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.0002571156150416324, 'time_algorithm_update': 0.014441605896977653, 'critic_loss': 9.699869670365986, 'actor_loss': 1.2298732650907416, 'time_step': 0.014755641507823564, 'td_error': 1.071835461672833, 'init_value': -0.2652181088924408, 'ave_value': -0.13779911031224976} step=342
2022-04-21 21:52.28 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220421215222/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-21 21:52.33 [info     ] TD3PlusBC_20220421215222: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.0002517797793561255, 'time_algorithm_update': 0.014669865892644515, 'critic_loss': 7.030128315875404, 'actor_loss': 0.9542868987858644, 'time_step': 0.014978113230208905, 'td_error': 1.064985021353233, 'init_value': -0.4531455636024475, 'ave_value': -0.2889099088989131} step=684
2022-04-21 21:52.33 [info     ] Model parameters are saved to d3rlpy_logs/TD3PlusBC_20220421215222/model_684.pt


...

2022-04-22 05:20.15 [info     ] FQE_20220422051752: epoch=49 step=16856 epoch=49 metrics={'time_sample_batch': 0.0001707160195638967, 'time_algorithm_update': 0.007619299167810485, 'loss': 0.6561122918799303, 'time_step': 0.007870377496231434, 'init_value': -22.68212890625, 'ave_value': -21.198855626475705, 'soft_opc': nan} step=16856


2022-04-22 05:20.15 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422051752/model_16856.pt


Epoch 50/50:   0%|          | 0/344 [00:00<?, ?it/s]

2022-04-22 05:20.18 [info     ] FQE_20220422051752: epoch=50 step=17200 epoch=50 metrics={'time_sample_batch': 0.00016948164895523425, 'time_algorithm_update': 0.007264900346134984, 'loss': 0.6519418475272264, 'time_step': 0.0075093972128491065, 'init_value': -22.730762481689453, 'ave_value': -21.599734639754594, 'soft_opc': nan} step=17200


2022-04-22 05:20.18 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220422051752/model_17200.pt


## Reading hyper params from file

In [19]:
with open("hyperparams_td3bc.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.005599980063978588, 0.0019551894944399694, 1.1846518566446107e-05, 1]
